### Create similarity features

In this tutorial we will look into another way of deriving features from other features - creating similarity features.

We will create a feature that compares the customer purchase patterns across product groups to all customers purchase patterns. We will first do bucketing at the customer level and at the overall level. Then we will compare the 2 dictionaries with the cosine similarity.

In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

16:43:45 | INFO     | Using configuration file at: /Users/viktor/.featurebyte/config.yaml
16:43:45 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)
16:43:45 | INFO     | SDK version: 0.6.0.dev121
16:43:45 | INFO     | No catalog activated.
16:43:46 | INFO     | 10 feature lists, 59 features deployed
16:43:46 | INFO     | Using profile: tutorial
16:43:46 | INFO     | Using configuration file at: /Users/viktor/.featurebyte/config.yaml
16:43:46 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)
16:43:46 | INFO     | SDK version: 0.6.0.dev121
16:43:46 | INFO     | No catalog activated.
16:43:46 | INFO     | 10 feature lists, 59 features deployed
16:43:47 | INFO     | Catalog activated: Grocery Dataset Tutorial


In [2]:
# Get view from GROCERYPRODUCT dimension table.
groceryproduct_view = catalog.get_view("GROCERYPRODUCT")
# Get view from INVOICEITEMS item table.
invoiceitems_view = catalog.get_view("INVOICEITEMS")

#### Join views 

In [3]:
# Join GROCERYPRODUCT view to INVOICEITEMS view.
invoiceitems_view = invoiceitems_view.join(groceryproduct_view, rsuffix="")

#### Create distribution features across |product groups

In [4]:
# Group INVOICEITEMS view by customer entity (GroceryCustomerGuid) across different ProductGroups.
invoiceitems_view_by_customer_across_productgroup =\
invoiceitems_view.groupby(
    ['GroceryCustomerGuid'], category="ProductGroup"
)

In [5]:
# Create Buckets representing the cumulative TotalCost of item, categorized by ProductGroup,
# for the customer over the past 26 weeks.
# The result is presented as a dictionary where the ProductGroup serves as the key
# and its corresponding sum of item TotalCost for the customer forms the value.
feature_group =\
invoiceitems_view_by_customer_across_productgroup.aggregate_over(
    "TotalCost", method=fb.AggFunc.SUM,
    feature_names=[
        "CUSTOMER_item_TotalCost_across_product_ProductGroups_26w"
    ],
    windows=["26w"]
)
# Get CUSTOMER_item_TotalCost_across_product_ProductGroups_26w object from feature group.
customer_item_totalcost_across_product_productgroups_26w =\
feature_group["CUSTOMER_item_TotalCost_across_product_ProductGroups_26w"]

In [6]:
# Group INVOICEITEMS view across different ProductGroups.
invoiceitems_view_by_overall_across_productgroup =\
invoiceitems_view.groupby([], category="ProductGroup")

In [7]:
# Create Buckets representing the cumulative TotalCost of item, categorized by ProductGroup,
# for ALL customers over the past 26 weeks.
# The result is presented as a dictionary where the ProductGroup serves as the key
# and its corresponding sum of item TotalCost forms the value.
feature_group =\
invoiceitems_view_by_overall_across_productgroup.aggregate_over(
    "TotalCost", method=fb.AggFunc.SUM,
    feature_names=[
        "OVERALL_item_TotalCost_across_product_ProductGroups_26w"
    ],
    windows=["26w"]
)
# Get OVERALL_item_TotalCost_across_product_ProductGroups_26w object from feature group.
overall_item_totalcost_across_product_productgroups_26w =\
feature_group["OVERALL_item_TotalCost_across_product_ProductGroups_26w"]

#### Derive Similarity feature across entities

In [8]:
# Derive Similarity feature from cosine similarity between
# CUSTOMER_item_TotalCost_across_product_ProductGroups_26w
# and OVERALL_item_TotalCost_across_product_ProductGroups_26w
customer_vs_overall_item_totalcost_across_product_productgroups_26w =\
customer_item_totalcost_across_product_productgroups_26w.cd.cosine_similarity(
        overall_item_totalcost_across_product_productgroups_26w
    )
# Give a name to new feature
customer_vs_overall_item_totalcost_across_product_productgroups_26w.name = \
"CUSTOMER_vs_OVERALL_item_TotalCost_across_product_ProductGroups_26w"

#### Preview feature

In [9]:
# Get observation table: 'Preview Table with 10 Customers'
preview_table = catalog.get_observation_table("Preview Table with 10 Customers").to_pandas()

In [10]:
# Preview CUSTOMER_item_TotalCost_across_product_ProductGroups_26w
customer_item_totalcost_across_product_productgroups_26w.preview(
    preview_table
)

POINT_IN_TIME                   GROCERYCUSTOMERGUID  \
0 2022-11-28 11:36:31  d4559f7d-eb28-42c6-b47d-847de24952c2   
1 2022-10-09 15:47:55  3f8c7c4c-f2c2-408e-a08e-622de3d3a0b9   
2 2022-09-14 15:42:42  35390325-8443-43c1-a934-18db923d9a47   
3 2022-12-26 18:39:46  4eb4ee84-ee13-4eec-9c26-61b6eb4ba35b   
4 2022-12-06 08:47:43  e42fa5f3-7737-4c6a-9ef4-856f113e60bd   
5 2022-11-09 12:14:40  8440debb-6abc-4adc-8c6c-749928141fd0   
6 2022-10-12 17:32:15  8a54e527-e9a4-47a9-a28f-8b3c6ecc02db   
7 2023-01-01 11:51:28  cea213d4-36e4-48c3-ae8d-c7a25911e11c   
8 2023-02-05 15:48:23  3b4f2821-b761-40e9-a32a-5f09685cc597   
9 2023-03-10 16:15:46  91a64566-e212-4e36-8f23-c1f1f324a301   

  CUSTOMER_item_TotalCost_across_product_ProductGroups_26w  
0  {\n  "Chips et Tortillas": 2.240000000000000e+...        
1  {\n  "Chips et Tortillas": 8.430000000000000e+...        
2  {\n  "Adoucissants et Soin du linge": 4.390000...        
3  {\n  "Animalerie, Soins et Hygiène": 5.4819999...        
4  {\n  "Aide à la Pâtisserie": 2.980000000000000...        
5  {\n  "Aide à la Pâtisserie": 2.380000000000000...        
6  {\n  "Adoucissants et Soin du linge": 2.000000...        
7  {\n  "Adoucissants et Soin du linge": 1.067000...        
8  {\n  "Aide à la Pâtisserie": 5.180000000000000...        
9  {\n  "Adoucissants et Soin du linge": 1.250000...

In [11]:
# Preview OVERALL_item_TotalCost_across_product_ProductGroups_26w
overall_item_totalcost_across_product_productgroups_26w.preview(
    preview_table
)

POINT_IN_TIME                   GROCERYCUSTOMERGUID  \
0 2022-11-28 11:36:31  d4559f7d-eb28-42c6-b47d-847de24952c2   
1 2022-10-09 15:47:55  3f8c7c4c-f2c2-408e-a08e-622de3d3a0b9   
2 2022-09-14 15:42:42  35390325-8443-43c1-a934-18db923d9a47   
3 2022-12-26 18:39:46  4eb4ee84-ee13-4eec-9c26-61b6eb4ba35b   
4 2022-12-06 08:47:43  e42fa5f3-7737-4c6a-9ef4-856f113e60bd   
5 2022-11-09 12:14:40  8440debb-6abc-4adc-8c6c-749928141fd0   
6 2022-10-12 17:32:15  8a54e527-e9a4-47a9-a28f-8b3c6ecc02db   
7 2023-01-01 11:51:28  cea213d4-36e4-48c3-ae8d-c7a25911e11c   
8 2023-02-05 15:48:23  3b4f2821-b761-40e9-a32a-5f09685cc597   
9 2023-03-10 16:15:46  91a64566-e212-4e36-8f23-c1f1f324a301   

  OVERALL_item_TotalCost_across_product_ProductGroups_26w  
0  {\n  "Adoucissants et Soin du linge": 1.120220...       
1  {\n  "Adoucissants et Soin du linge": 1.108720...       
2  {\n  "Adoucissants et Soin du linge": 1.095090...       
3  {\n  "Adoucissants et Soin du linge": 1.181730...       
4  {\n  "Adoucissants et Soin du linge": 1.121930...       
5  {\n  "Adoucissants et Soin du linge": 1.145870...       
6  {\n  "Adoucissants et Soin du linge": 1.141140...       
7  {\n  "Adoucissants et Soin du linge": 1.217740...       
8  {\n  "Adoucissants et Soin du linge": 1.209600...       
9  {\n  "Adoucissants et Soin du linge": 1.231790...

In [12]:
# Preview CUSTOMER_vs_OVERALL_item_TotalCost_across_product_ProductGroups_26w
customer_vs_overall_item_totalcost_across_product_productgroups_26w.preview(
    preview_table
)

POINT_IN_TIME                   GROCERYCUSTOMERGUID  \
0 2022-11-28 11:36:31  d4559f7d-eb28-42c6-b47d-847de24952c2   
1 2022-10-09 15:47:55  3f8c7c4c-f2c2-408e-a08e-622de3d3a0b9   
2 2022-09-14 15:42:42  35390325-8443-43c1-a934-18db923d9a47   
3 2022-12-26 18:39:46  4eb4ee84-ee13-4eec-9c26-61b6eb4ba35b   
4 2022-12-06 08:47:43  e42fa5f3-7737-4c6a-9ef4-856f113e60bd   
5 2022-11-09 12:14:40  8440debb-6abc-4adc-8c6c-749928141fd0   
6 2022-10-12 17:32:15  8a54e527-e9a4-47a9-a28f-8b3c6ecc02db   
7 2023-01-01 11:51:28  cea213d4-36e4-48c3-ae8d-c7a25911e11c   
8 2023-02-05 15:48:23  3b4f2821-b761-40e9-a32a-5f09685cc597   
9 2023-03-10 16:15:46  91a64566-e212-4e36-8f23-c1f1f324a301   

   CUSTOMER_vs_OVERALL_item_TotalCost_across_product_ProductGroups_26w  
0                                           0.466220                    
1                                           0.558564                    
2                                           0.872762                    
3                                           0.713610                    
4                                           0.657608                    
5                                           0.509610                    
6                                           0.753250                    
7                                           0.561260                    
8                                           0.761539                    
9                                           0.729546

#### Save feature

In [13]:
# Save feature
customer_vs_overall_item_totalcost_across_product_productgroups_26w.save()

Done! |████████████████████████████████████████| 100% in 6.5s (0.16%/s)         


#### As always, add description and view definition file

In [14]:
# Add description
customer_vs_overall_item_totalcost_across_product_productgroups_26w.update_description(
    "Similarity between the customer and all customers measured by the "
    "Cosine Similarity between the Distribution representing the cumulative"
    " TotalCost of item,  categorized by their respective product's "
    "ProductGroup, over 26w for both entities."
)
# See feature definition file
customer_vs_overall_item_totalcost_across_product_productgroups_26w.definition

'# Generated by SDK version: 0.6.0.dev121\nfrom bson import ObjectId\nfrom featurebyte import DimensionTable\nfrom featurebyte import FeatureJobSetting\nfrom featurebyte import ItemTable\n\n\n# item_table name: "INVOICEITEMS", event_table name: "GROCERYINVOICE"\nitem_table = ItemTable.get_by_id(ObjectId("6564b7ecbeba6c193e0fe3bd"))\nitem_view = item_table.get_view(\n    event_suffix=None,\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[],\n    event_drop_column_names=["record_available_at"],\n    event_column_cleaning_operations=[],\n    event_join_column_names=[\n        "Timestamp",\n        "GroceryInvoiceGuid",\n        "GroceryCustomerGuid",\n        "tz_offset",\n    ],\n)\n\n# dimension_table name: "GROCERYPRODUCT"\ndimension_table = DimensionTable.get_by_id(ObjectId("6564b7edbeba6c193e0fe3be"))\ndimension_view = dimension_table.get_view(\n    view_mode="manual", drop_column_names=[], column_cleaning_operations=[]\n)\njoined_view = item_view.join(\n    dimension_view, on="GroceryProductGuid", how="left", rsuffix="", rprefix=""\n)\ngrouped = joined_view.groupby(\n    by_keys=[], category="ProductGroup"\n).aggregate_over(\n    value_column="TotalCost",\n    method="sum",\n    windows=["26w"],\n    feature_names=["OVERALL_item_TotalCost_across_product_ProductGroups_26w"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", frequency="3600s", time_modulo_frequency="120s"\n    ),\n    skip_fill_na=True,\n)\nfeat = grouped["OVERALL_item_TotalCost_across_product_ProductGroups_26w"]\ngrouped_1 = joined_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category="ProductGroup"\n).aggregate_over(\n    value_column="TotalCost",\n    method="sum",\n    windows=["26w"],\n    feature_names=["CUSTOMER_item_TotalCost_across_product_ProductGroups_26w"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", frequency="3600s", time_modulo_frequency="120s"\n    ),\n    skip_fill_na=True,\n)\nfeat_1 = grouped_1["CUSTOMER_item_TotalCost_across_product_ProductGroups_26w"]\nfeat_2 = feat_1.cd.cosine_similarity(other=feat)\nfeat_2.name = (\n    "CUSTOMER_vs_OVERALL_item_TotalCost_across_product_ProductGroups_26w"\n)\noutput = feat_2\noutput.save(_id=ObjectId("6564b93614db530858940f50"))\n'

### Concepts in this tutorial
- [View Joins](https://docs.featurebyte.com/latest/about/glossary/#view-join)
- [Feature Transforms](https://docs.featurebyte.com/latest/about/glossary/#feature-transforms)
- [Cross Aggregate features](https://docs.featurebyte.com/latest/about/glossary/#cross-aggregate-features)

#### SDK reference for
- [Feature.cd.cosine_similarity()](https://docs.featurebyte.com/latest/reference/featurebyte.Feature.cd.cosine_similarity/)